In [127]:
import pandas as pd
import matplotlib.pyplot as plt
import re
import time
import warnings
import numpy as np
import nltk
from nltk.corpus import stopwords
from sklearn.preprocessing import normalize
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
warnings.filterwarnings("ignore")
import sys
import os 
import pandas as pd
import numpy as np
from tqdm import tqdm
import spacy

from nltk.corpus import stopwords
from nltk.stem import PorterStemmer








In [128]:
path = os.path.join('Data','Preprocessed_with_fuzz.csv')
data = pd.read_csv(path)
data

id    qid1    qid2  \
0            0       1       2   
1            1       3       4   
2            2       5       6   
3            3       7       8   
4            4       9      10   
...        ...     ...     ...   
404282  404285  433578  379845   
404283  404286   18840  155606   
404284  404287  537928  537929   
404285  404288  537930  537931   
404286  404289  537932  537933   

                                                question1  \
0                step step guid invest share market india   
1                       stori kohinoor koh i noor diamond   
2                  increas speed internet connect use vpn   
3                                        mental lone solv   
4       one dissolv water quikli sugar salt methan car...   
...                                                   ...   
404282  mani keyword racket program languag latest ver...   
404283                                  believ life death   
404284                                           one coin   
404285  approx annual cost live studi uic chicago indi...   
404286                                    like sex cousin   

                                                question2  is_duplicate  \
0                      step step guid invest share market             0   
1       would happen indian govern stole kohinoor koh ...             0   
2                          internet speed increas hack dn             0   
3                            find remaind math math divid             0   
4                            fish would surviv salt water             0   
...                                                   ...           ...   
404282   mani keyword perl program languag latest version             0   
404283                                    true life death             1   
404284                                           own coin             0   
404285  littl hairfal problem want use hair style prod...             0   
404286                                    like sex cousin             0   

           r_len  q1_words  q2_words  c_words  token_set_ratio  \
0       1.157895        14        12       10              100   
1       0.579545         8        13        4               90   
2       1.237288        14        10        4               85   
3       0.769231        11         9        0               26   
4       1.948718        13         7        2               53   
...          ...       ...       ...      ...              ...   
404282  1.075949        14        13       11               95   
404283  0.976190         8         9        5               80   
404284  1.000000         4         3        1               88   
404285  0.740157        17        25        1               37   
404286  0.822222         8        10        8              100   

        token_sort_ratio  fuzz_ratio  fuzz_partial_ratio  
0                     92          92                 100  
1                     63          63                  94  
2                     74          56                  60  
3                     27          27                  31  
4                     42          42                  50  
...                  ...         ...                 ...  
404282                88          92                  90  
404283                62          75                  80  
404284                88          88                  88  
404285                37          36                  41  
404286               100         100                 100  

[404287 rows x 14 columns]

In [129]:

from tqdm.notebook import tqdm
tqdm.pandas()
data['question1'] = data['question1'].progress_apply(lambda x: str(x))
data['question2'] = data['question2'].progress_apply(lambda x: str(x))

  0%|          | 0/404287 [00:00<?, ?it/s]

  0%|          | 0/404287 [00:00<?, ?it/s]

In [130]:
questions = data['question1'].values
questions = questions.tolist()
print(len(questions))
questions.extend(data['question2'].values.tolist())
print(len(questions))

404287
808574


In [131]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
# merge texts


tfidf = TfidfVectorizer(lowercase=False, )
tfidf.fit_transform(questions)

# dict key:word and value:tf-idf score
word2tfidf = dict(zip(tfidf.get_feature_names(), tfidf.idf_))
word2tfidf

{'aa': 10.52549127416971,
 'aaa': 11.076668193459268,
 'aaac': 13.216734356955538,
 'aaadhar': 13.909881537515483,
 'aaai': 13.909881537515483,
 'aabb': 13.909881537515483,
 'aac': 12.523587176395592,
 'aachar': 12.657118569020115,
 'aachen': 12.038079360613892,
 'aad': 13.909881537515483,
 'aadaab': 13.50441642940732,
 'aadam': 13.909881537515483,
 'aadh': 13.909881537515483,
 'aadhaar': 9.605816444311314,
 'aadhar': 9.727831394874277,
 'aadharcard': 13.909881537515483,
 'aadmi': 10.818839084157167,
 'aadmk': 13.50441642940732,
 'aadvantag': 13.216734356955538,
 'aae': 13.50441642940732,
 'aafreen': 13.909881537515483,
 'aaft': 13.909881537515483,
 'aag': 13.909881537515483,
 'aah': 13.50441642940732,
 'aaha': 13.909881537515483,
 'aahat': 13.216734356955538,
 'aahista': 13.909881537515483,
 'aai': 12.038079360613892,
 'aaj': 13.216734356955538,
 'aakash': 10.731827707167538,
 'aaksh': 13.909881537515483,
 'aalavandhan': 13.909881537515483,
 'aaloma': 13.909881537515483,
 'aalto': 13.

In [132]:
import spacy
# en_vectors_web_lg, which includes over 1 million unique vectors.
nlp = spacy.load('en_core_web_sm')

vecs1 = []
s=0
for qu1 in tqdm(list(data['question1'])):
    doc1 = nlp(qu1) 
    # 96 is the number of dimensions of vectors 
    mean_vec1 = np.zeros([len(doc1), len(doc1[0].vector)])
    for word1 in doc1:
        # word2vec
        vec1 = word1.vector
        # fetch df score
        try:
            idf = word2tfidf[str(word1)]
        except:
            idf = 0
        # compute final vec
        mean_vec1 += vec1 * idf

    mean_vec1 = mean_vec1.mean(axis=0)
    vecs1.append(mean_vec1)
    vecs1

  0%|          | 0/404287 [00:00<?, ?it/s]

In [133]:
vecs1

[array([ 14.30296975,  23.78243554,  35.48607713,   7.61711448,
          7.33533835,   0.94621673, -17.00539911,  14.79346246,
         -6.11065217,  12.05869198,   0.09796662, -34.41979504,
         31.01149416, -15.26658428,   0.84450269,  42.24038678,
         -4.45592654,  20.35279256,  12.65613428,  47.70745732,
        -31.04414809, -31.70850468,  23.03462362, -22.319157  ,
         -6.1504305 , -17.49600053, -33.72534156, -25.19492602,
         11.57321695,  -3.18830378,  24.70743585, -23.92660314,
        -12.88693416, -20.52793431,  28.21188092, -34.11278844,
        -21.7451953 ,  17.91806859,  -9.04720116,  38.5507859 ,
        -44.2546702 ,   2.15045446,   6.13107144,  18.70736867,
         -4.75345773,  22.84454402,   9.41315739, -14.34369101,
         34.87454009, -11.95904112,  18.60680234, -11.71187709,
         -7.02787044, -34.05534489,  -2.01550934,  41.17494553,
        -17.75685233,  14.39905688,  -8.20069513,  12.81512487,
        -11.98596445, -11.54642707, -28.

In [134]:
vecs2 = []
for qu2 in tqdm(list(data['question2'])):
    doc2 = nlp(qu2) 
    mean_vec2 = np.zeros([len(doc2), len(doc2[0].vector)])
    for word2 in doc2:
        # word2vec
        vec2 = word2.vector
        # fetch df score
        try:
            idf = word2tfidf[str(word2)]
        except:
            #print word
            idf = 0
        # compute final vec
        mean_vec2 += vec2 * idf
    mean_vec2 = mean_vec2.mean(axis=0)
    vecs2.append(mean_vec2)


  0%|          | 0/404287 [00:00<?, ?it/s]

In [135]:
vecs2

[array([ 1.17748868e+01,  2.66100637e+01,  3.81143885e+01,  1.56493617e+01,
         2.28750265e+00,  5.19248451e+00, -1.51219455e+01,  1.47558115e+01,
        -7.07578057e+00,  6.58207870e+00, -4.02811185e+00, -2.74992570e+01,
         2.51901925e+01, -2.23050071e+01, -5.20078647e+00,  2.90800837e+01,
        -4.49436307e-02,  1.64132321e+01,  1.74734785e+01,  4.87887813e+01,
        -2.62056504e+01, -2.75192096e+01,  2.25739573e+01, -1.78619375e+01,
        -2.80742312e+00, -1.42116673e+01, -3.34152641e+01, -2.30083981e+01,
         1.17129520e+01, -3.94102485e+00,  2.25006654e+01, -2.23283825e+01,
        -1.46689335e+01, -2.39404019e+01,  1.84044721e+01, -2.63152359e+01,
        -2.40693716e+01,  4.82469612e+00, -7.16854863e+00,  3.64878073e+01,
        -3.96964273e+01, -1.44205689e-02,  8.94117042e+00,  2.01921647e+01,
        -7.50658655e+00,  2.78493497e+01,  1.00390697e+01, -1.45391810e+01,
         3.87213613e+01, -9.08426929e+00,  1.57059529e+01, -1.25481816e+01,
        -1.9

In [138]:
column_names_q1=[]
column_names_q2=[]
for i in range(0,96):
    column_names_q1.append(str(i)+'q1')
    column_names_q2.append(str(i)+'q2')

In [139]:
vec1 = pd.DataFrame(vecs1,columns = column_names_q1)
vec1

0q1        1q1        2q1        3q1        4q1        5q1  \
0       14.302970  23.782436  35.486077   7.617114   7.335338   0.946217   
1       -8.789968 -17.118239  16.274424  10.178653  21.435574   6.624891   
2       27.569262  26.354036   8.885428  -7.944374  11.193249  -3.523705   
3      -14.796216  12.977406   7.950473  -2.766888   3.853418   4.621763   
4       22.944094  59.336985  16.939992  -2.087996  -9.012983 -29.934223   
...           ...        ...        ...        ...        ...        ...   
404282  40.758385 -10.830759  17.822650  -5.091871  -1.431602 -23.909204   
404283   8.703464   0.955755  -4.836804  -2.335064   9.713145   6.791476   
404284 -10.312027   6.719791   1.134819   6.488420   2.448784   3.819964   
404285  13.646165  17.263480   7.684294 -11.386293   6.708778 -26.733201   
404286   5.019762   2.755696   5.654860  10.955379   2.109948   0.487034   

              6q1        7q1        8q1        9q1  ...       86q1       87q1  \
0      -17.005399  14.793462  -6.110652  12.058692  ...  20.665396 -14.803937   
1       -3.875764   2.730949  -6.707454   5.621727  ...  15.259817 -19.290593   
2      -13.908291   6.138206  -3.868167  32.978834  ...   8.478983 -26.561904   
3      -11.486523   2.552353  -4.134310   6.124308  ...  -2.711233 -17.162654   
4      -51.270855  43.197311 -34.398048  38.244764  ...  14.618898 -58.699728   
...           ...        ...        ...        ...  ...        ...        ...   
404282 -35.421285  17.057855 -27.008186  16.939402  ...  -1.467686  -0.217883   
404283  -6.063017  -2.899312  -2.983640   6.038107  ...  -0.420657 -11.083950   
404284 -12.239960  12.950583  -0.953057  13.441961  ...  -6.214589  -6.735012   
404285 -22.798921  17.910229 -23.679332   3.926802  ... -12.141921 -11.909467   
404286 -16.365653  -2.042072   2.343383  11.905017  ...   0.600433   1.283406   

             88q1       89q1       90q1       91q1       92q1       93q1  \
0      -23.228240 -44.430750 -25.585940 -15.086276  10.636340  43.627511   
1      -50.764602 -25.137020  -8.872656 -31.904802   3.595542  14.486567   
2       -9.875064 -14.686690 -25.156424 -22.811990   3.664527  35.545111   
3      -13.096301 -29.100321   9.639945  -0.639065  17.495471  26.208816   
4        1.862809 -74.766355  -5.273436 -35.553544  24.814307  14.633631   
...           ...        ...        ...        ...        ...        ...   
404282  -0.330217 -37.048026  -8.141094 -35.156172  -4.488042  13.171619   
404283  -4.122587 -18.726519  -9.277322 -18.336970  -3.600506  14.540848   
404284 -13.140872  -3.090642 -14.283928  -8.580930  -0.776581   6.534907   
404285 -18.078644 -28.416584  44.205804 -28.093339  40.513746  36.223719   
404286 -15.643097  -2.210714  -2.253333   3.119341  -3.032176   3.198808   

             94q1       95q1  
0      -14.711026   7.424150  
1        6.439931  19.409613  
2        9.342839 -14.891584  
3        7.353994   6.476805  
4      -49.818433  -6.386695  
...           ...        ...  
404282 -13.414104   9.306400  
404283  12.355465  -0.385216  
404284   7.763345  -7.741871  
404285 -26.917440   7.989453  
404286   4.019858   0.414988  

[404287 rows x 96 columns]

In [140]:
vec2 = pd.DataFrame(vecs2,columns=column_names_q2)
vec2

[array([ 1.17748868e+01,  2.66100637e+01,  3.81143885e+01,  1.56493617e+01,
         2.28750265e+00,  5.19248451e+00, -1.51219455e+01,  1.47558115e+01,
        -7.07578057e+00,  6.58207870e+00, -4.02811185e+00, -2.74992570e+01,
         2.51901925e+01, -2.23050071e+01, -5.20078647e+00,  2.90800837e+01,
        -4.49436307e-02,  1.64132321e+01,  1.74734785e+01,  4.87887813e+01,
        -2.62056504e+01, -2.75192096e+01,  2.25739573e+01, -1.78619375e+01,
        -2.80742312e+00, -1.42116673e+01, -3.34152641e+01, -2.30083981e+01,
         1.17129520e+01, -3.94102485e+00,  2.25006654e+01, -2.23283825e+01,
        -1.46689335e+01, -2.39404019e+01,  1.84044721e+01, -2.63152359e+01,
        -2.40693716e+01,  4.82469612e+00, -7.16854863e+00,  3.64878073e+01,
        -3.96964273e+01, -1.44205689e-02,  8.94117042e+00,  2.01921647e+01,
        -7.50658655e+00,  2.78493497e+01,  1.00390697e+01, -1.45391810e+01,
         3.87213613e+01, -9.08426929e+00,  1.57059529e+01, -1.25481816e+01,
        -1.9

In [142]:
data=pd.concat([data,vec1,vec2],axis=1)

In [143]:
data

id    qid1    qid2  \
0            0       1       2   
1            1       3       4   
2            2       5       6   
3            3       7       8   
4            4       9      10   
...        ...     ...     ...   
404282  404285  433578  379845   
404283  404286   18840  155606   
404284  404287  537928  537929   
404285  404288  537930  537931   
404286  404289  537932  537933   

                                                question1  \
0                step step guid invest share market india   
1                       stori kohinoor koh i noor diamond   
2                  increas speed internet connect use vpn   
3                                        mental lone solv   
4       one dissolv water quikli sugar salt methan car...   
...                                                   ...   
404282  mani keyword racket program languag latest ver...   
404283                                  believ life death   
404284                                           one coin   
404285  approx annual cost live studi uic chicago indi...   
404286                                    like sex cousin   

                                                question2  is_duplicate  \
0                      step step guid invest share market             0   
1       would happen indian govern stole kohinoor koh ...             0   
2                          internet speed increas hack dn             0   
3                            find remaind math math divid             0   
4                            fish would surviv salt water             0   
...                                                   ...           ...   
404282   mani keyword perl program languag latest version             0   
404283                                    true life death             1   
404284                                           own coin             0   
404285  littl hairfal problem want use hair style prod...             0   
404286                                    like sex cousin             0   

           r_len  q1_words  q2_words  c_words  ...       86q2       87q2  \
0       1.157895        14        12       10  ...  18.996169 -20.792302   
1       0.579545         8        13        4  ...  14.065927 -32.599546   
2       1.237288        14        10        4  ... -10.416016 -22.239469   
3       0.769231        11         9        0  ...   5.878617 -14.109877   
4       1.948718        13         7        2  ...  17.013748  -8.558105   
...          ...       ...       ...      ...  ...        ...        ...   
404282  1.075949        14        13       11  ...   5.165456 -11.464328   
404283  0.976190         8         9        5  ... -10.910187 -17.369496   
404284  1.000000         4         3        1  ...   1.919942  -8.093113   
404285  0.740157        17        25        1  ...  30.862432 -37.270439   
404286  0.822222         8        10        8  ...   0.600433   1.283406   

             88q2       89q2       90q2       91q2       92q2       93q2  \
0      -22.099690 -39.491452 -25.912614 -12.067960  16.488814  40.195788   
1      -54.725100   5.573329 -19.255911 -20.936302  14.818417  39.671840   
2       -7.408381 -20.735026 -12.088432 -12.295888 -10.115664  35.265050   
3      -15.244852  -6.924014  -9.974960 -26.881352   0.288322  38.630093   
4      -20.063761   2.328464 -28.234996 -12.931378   0.076697  22.908110   
...           ...        ...        ...        ...        ...        ...   
404282  -1.075705 -48.533878  -5.871400 -31.292594  -2.277079  10.066749   
404283  -5.371824  -7.351629  -1.781602  -5.029964   7.696611   6.667526   
404284  -4.486509  -4.305888  -0.647508   6.759025   2.776058   9.318659   
404285 -49.603633  37.502799 -39.455253 -51.782338  21.501225  58.417728   
404286 -15.643097  -2.210714  -2.253333   3.119341  -3.032176   3.198808   

             94q2       95q2  
0      -14.407949  -2.594384  
1       10.103314   9.297360  
2       16.605785  16.955342  
3        3.197422  

In [146]:
data.to_csv('Data/data_with_vectors.csv')

In [145]:
data

id    qid1    qid2  \
0            0       1       2   
1            1       3       4   
2            2       5       6   
3            3       7       8   
4            4       9      10   
...        ...     ...     ...   
404282  404285  433578  379845   
404283  404286   18840  155606   
404284  404287  537928  537929   
404285  404288  537930  537931   
404286  404289  537932  537933   

                                                question1  \
0                step step guid invest share market india   
1                       stori kohinoor koh i noor diamond   
2                  increas speed internet connect use vpn   
3                                        mental lone solv   
4       one dissolv water quikli sugar salt methan car...   
...                                                   ...   
404282  mani keyword racket program languag latest ver...   
404283                                  believ life death   
404284                                           one coin   
404285  approx annual cost live studi uic chicago indi...   
404286                                    like sex cousin   

                                                question2  is_duplicate  \
0                      step step guid invest share market             0   
1       would happen indian govern stole kohinoor koh ...             0   
2                          internet speed increas hack dn             0   
3                            find remaind math math divid             0   
4                            fish would surviv salt water             0   
...                                                   ...           ...   
404282   mani keyword perl program languag latest version             0   
404283                                    true life death             1   
404284                                           own coin             0   
404285  littl hairfal problem want use hair style prod...             0   
404286                                    like sex cousin             0   

           r_len  q1_words  q2_words  c_words  ...       86q2       87q2  \
0       1.157895        14        12       10  ...  18.996169 -20.792302   
1       0.579545         8        13        4  ...  14.065927 -32.599546   
2       1.237288        14        10        4  ... -10.416016 -22.239469   
3       0.769231        11         9        0  ...   5.878617 -14.109877   
4       1.948718        13         7        2  ...  17.013748  -8.558105   
...          ...       ...       ...      ...  ...        ...        ...   
404282  1.075949        14        13       11  ...   5.165456 -11.464328   
404283  0.976190         8         9        5  ... -10.910187 -17.369496   
404284  1.000000         4         3        1  ...   1.919942  -8.093113   
404285  0.740157        17        25        1  ...  30.862432 -37.270439   
404286  0.822222         8        10        8  ...   0.600433   1.283406   

             88q2       89q2       90q2       91q2       92q2       93q2  \
0      -22.099690 -39.491452 -25.912614 -12.067960  16.488814  40.195788   
1      -54.725100   5.573329 -19.255911 -20.936302  14.818417  39.671840   
2       -7.408381 -20.735026 -12.088432 -12.295888 -10.115664  35.265050   
3      -15.244852  -6.924014  -9.974960 -26.881352   0.288322  38.630093   
4      -20.063761   2.328464 -28.234996 -12.931378   0.076697  22.908110   
...           ...        ...        ...        ...        ...        ...   
404282  -1.075705 -48.533878  -5.871400 -31.292594  -2.277079  10.066749   
404283  -5.371824  -7.351629  -1.781602  -5.029964   7.696611   6.667526   
404284  -4.486509  -4.305888  -0.647508   6.759025   2.776058   9.318659   
404285 -49.603633  37.502799 -39.455253 -51.782338  21.501225  58.417728   
404286 -15.643097  -2.210714  -2.253333   3.119341  -3.032176   3.198808   

             94q2       95q2  
0      -14.407949  -2.594384  
1       10.103314   9.297360  
2       16.605785  16.955342  
3        3.197422  

In [ ]:
data.to_csv('Data/data_with_vectors.csv')



In [147]:
data = pd.read_csv('Data/data_with_vectors.csv')
data.columns

Index(['Unnamed: 0', 'id', 'qid1', 'qid2', 'question1', 'question2',
       'is_duplicate', 'r_len', 'q1_words', 'q2_words',
       ...
       '86q2', '87q2', '88q2', '89q2', '90q2', '91q2', '92q2', '93q2', '94q2',
       '95q2'],
      dtype='object', length=207)

In [149]:
data.drop(['Unnamed: 0'],axis = 1,inplace = True)

In [150]:
data

id    qid1    qid2  \
0            0       1       2   
1            1       3       4   
2            2       5       6   
3            3       7       8   
4            4       9      10   
...        ...     ...     ...   
404282  404285  433578  379845   
404283  404286   18840  155606   
404284  404287  537928  537929   
404285  404288  537930  537931   
404286  404289  537932  537933   

                                                question1  \
0                step step guid invest share market india   
1                       stori kohinoor koh i noor diamond   
2                  increas speed internet connect use vpn   
3                                        mental lone solv   
4       one dissolv water quikli sugar salt methan car...   
...                                                   ...   
404282  mani keyword racket program languag latest ver...   
404283                                  believ life death   
404284                                           one coin   
404285  approx annual cost live studi uic chicago indi...   
404286                                    like sex cousin   

                                                question2  is_duplicate  \
0                      step step guid invest share market             0   
1       would happen indian govern stole kohinoor koh ...             0   
2                          internet speed increas hack dn             0   
3                            find remaind math math divid             0   
4                            fish would surviv salt water             0   
...                                                   ...           ...   
404282   mani keyword perl program languag latest version             0   
404283                                    true life death             1   
404284                                           own coin             0   
404285  littl hairfal problem want use hair style prod...             0   
404286                                    like sex cousin             0   

           r_len  q1_words  q2_words  c_words  ...       86q2       87q2  \
0       1.157895        14        12       10  ...  18.996169 -20.792302   
1       0.579545         8        13        4  ...  14.065927 -32.599546   
2       1.237288        14        10        4  ... -10.416016 -22.239469   
3       0.769231        11         9        0  ...   5.878617 -14.109877   
4       1.948718        13         7        2  ...  17.013748  -8.558105   
...          ...       ...       ...      ...  ...        ...        ...   
404282  1.075949        14        13       11  ...   5.165456 -11.464328   
404283  0.976190         8         9        5  ... -10.910187 -17.369496   
404284  1.000000         4         3        1  ...   1.919942  -8.093113   
404285  0.740157        17        25        1  ...  30.862432 -37.270439   
404286  0.822222         8        10        8  ...   0.600433   1.283406   

             88q2       89q2       90q2       91q2       92q2       93q2  \
0      -22.099690 -39.491452 -25.912614 -12.067960  16.488814  40.195788   
1      -54.725100   5.573329 -19.255911 -20.936302  14.818417  39.671840   
2       -7.408381 -20.735026 -12.088432 -12.295888 -10.115664  35.265050   
3      -15.244852  -6.924014  -9.974960 -26.881352   0.288322  38.630093   
4      -20.063761   2.328464 -28.234996 -12.931378   0.076697  22.908110   
...           ...        ...        ...        ...        ...        ...   
404282  -1.075705 -48.533878  -5.871400 -31.292594  -2.277079  10.066749   
404283  -5.371824  -7.351629  -1.781602  -5.029964   7.696611   6.667526   
404284  -4.486509  -4.305888  -0.647508   6.759025   2.776058   9.318659   
404285 -49.603633  37.502799 -39.455253 -51.782338  21.501225  58.417728   
404286 -15.643097  -2.210714  -2.253333   3.119341  -3.032176   3.198808   

             94q2       95q2  
0      -14.407949  -2.594384  
1       10.103314   9.297360  
2       16.605785  16.955342  
3        3.197422  

In [152]:
data.to_csv('Data/data_with_vectors.csv')



In [153]:
data = pd.read_csv('Data/data_with_vectors.csv')

In [154]:
data

Unnamed: 0      id    qid1    qid2  \
0                0       0       1       2   
1                1       1       3       4   
2                2       2       5       6   
3                3       3       7       8   
4                4       4       9      10   
...            ...     ...     ...     ...   
404282      404282  404285  433578  379845   
404283      404283  404286   18840  155606   
404284      404284  404287  537928  537929   
404285      404285  404288  537930  537931   
404286      404286  404289  537932  537933   

                                                question1  \
0                step step guid invest share market india   
1                       stori kohinoor koh i noor diamond   
2                  increas speed internet connect use vpn   
3                                        mental lone solv   
4       one dissolv water quikli sugar salt methan car...   
...                                                   ...   
404282  mani keyword racket program languag latest ver...   
404283                                  believ life death   
404284                                           one coin   
404285  approx annual cost live studi uic chicago indi...   
404286                                    like sex cousin   

                                                question2  is_duplicate  \
0                      step step guid invest share market             0   
1       would happen indian govern stole kohinoor koh ...             0   
2                          internet speed increas hack dn             0   
3                            find remaind math math divid             0   
4                            fish would surviv salt water             0   
...                                                   ...           ...   
404282   mani keyword perl program languag latest version             0   
404283                                    true life death             1   
404284                                           own coin             0   
404285  littl hairfal problem want use hair style prod...             0   
404286                                    like sex cousin             0   

           r_len  q1_words  q2_words  ...       86q2       87q2       88q2  \
0       1.157895        14        12  ...  18.996169 -20.792302 -22.099690   
1       0.579545         8        13  ...  14.065927 -32.599546 -54.725100   
2       1.237288        14        10  ... -10.416016 -22.239469  -7.408381   
3       0.769231        11         9  ...   5.878617 -14.109877 -15.244852   
4       1.948718        13         7  ...  17.013748  -8.558105 -20.063761   
...          ...       ...       ...  ...        ...        ...        ...   
404282  1.075949        14        13  ...   5.165456 -11.464328  -1.075705   
404283  0.976190         8         9  ... -10.910187 -17.369496  -5.371824   
404284  1.000000         4         3  ...   1.919942  -8.093113  -4.486509   
404285  0.740157        17        25  ...  30.862432 -37.270439 -49.603633   
404286  0.822222         8        10  ...   0.600433   1.283406 -15.643097   

             89q2       90q2       91q2       92q2       93q2       94q2  \
0      -39.491452 -25.912614 -12.067960  16.488814  40.195788 -14.407949   
1        5.573329 -19.255911 -20.936302  14.818417  39.671840  10.103314   
2      -20.735026 -12.088432 -12.295888 -10.115664  35.265050  16.605785   
3       -6.924014  -9.974960 -26.881352   0.288322  38.630093   3.197422   
4        2.328464 -28.234996 -12.931378   0.076697  22.908110  -0.293697   
...           ...        ...        ...        ...        ...        ...   
404282 -48.533878  -5.871400 -31.292594  -2.277079  10.066749 -26.098974   
404283  -7.351629  -1.781602  -5.029964   7.696611   6.667526   8.021969   
404284  -4.305888  -0.647508   6.759025   2.776058   9.318659   3.572573   
404285  37.502799 -39.455253 -51.782338  21.501225  58.417728  -7.236231   
404286  -2.210714  -2.253333   3.119341  -3.0321